## Importing relevant libraries

In [1]:
import numpy as np
import matplotlib.pyplot as plt

# ## Get the ansatz types from Qiskit
# from qiskit.circuit.library import RealAmplitudes, TwoLocal, EfficientSU2

## Function for plotting for a particular performance metric

In [3]:
def convert_to_log_scale(values):
    """
    Convert values to a representation in powers of 10 (e.g., 0.04 becomes 10^{-2}).

    Args:
        values (list or np.array): List or array of numerical values.

    Returns:
        list: List of values in the format 10^{exponent} as strings.
    """
    powers_of_10 = []
    for value in values:
        if value == 0:
            powers_of_10.append("0")  # Handle zero separately
        else:
            exponent = int(np.floor(np.log10(abs(value))))
            powers_of_10.append(f"$10^{{{exponent}}}$")
    
    return powers_of_10

def plot_metric(data, ax, metric_name, ylabel):
    import numpy as np

    # Extract the optimizers, ansatze, and the specified metric
    optimizers = ['SLSQP', 'P_BFGS', 'NELDER_MEAD', 'POWELL']
    ansatze = ['RealAmplitudes', 'TwoLocal', 'EfficientSU2']
    colors = ['blue', 'red', 'purple']  # Color map for ansatze
    markers = {'RealAmplitudes': 'o', 'TwoLocal': 's', 'EfficientSU2': '^'}

    # Data organization by optimizer and ansatz
    optimizer_data = {opt: {ansatz: [] for ansatz in ansatze} for opt in optimizers}
    failed_data = {opt: {ansatz: [] for ansatz in ansatze} for opt in optimizers}

    for entry in data:
        optimizer, value = entry
        opt, ansatz = optimizer.split('-')

        if value == 0:  # Mark as 'Did not converge'
            failed_data[opt][ansatz].append(entry)
        else:
            optimizer_data[opt][ansatz].append(value)

    # Plotting the metric for each optimizer and ansatz
    x_positions = np.arange(len(optimizers))
    offset = 0.1  # Base horizontal offset for non-converging cases
    vertical_offset = 0.5  # Vertical offset for crosses

    # Plot the failed cases (crosses) first
    for i, opt in enumerate(optimizers):
        for j, ansatz in enumerate(ansatze):
            failed_cases = failed_data[opt][ansatz]

            # Plot the non-converging cases
            if failed_cases:
                for k, _ in enumerate(failed_cases):
                    ax.scatter(
                        x_positions[i] + offset * (j - 1),  # Horizontal offset based on ansatz index
                        0 + vertical_offset * (k - len(failed_cases) // 2),  # Vertical offset to spread crosses
                        color=colors[j], marker='x', s=100, label=f'{ansatz} (NC)' if i == 0 and j == 0 else ""
                    )

    # Plot the metric values for converging cases
    for i, opt in enumerate(optimizers):
        for j, ansatz in enumerate(ansatze):
            values = optimizer_data[opt][ansatz]

            # Plot the metric values with specific markers for ansatze
            if values:
                ax.plot(
                    [x_positions[i]], values,
                    marker=markers[ansatz], markersize=9, linestyle='-', color=colors[j],
                    label=ansatz if i == 0 else ""  # Only add the ansatz label once
                )

    # Set axis properties
    ax.set_xticks(x_positions)
    ax.set_xticklabels(optimizers)
    ax.set_ylabel(ylabel, fontsize=20)
    ax.tick_params(axis='x', labelsize=14)
    ax.tick_params(axis='y', labelsize=17)
    ax.grid(True)
    ax.legend(fontsize=15)

def plot_metric_log(data, ax, metric_name, ylabel):
    import numpy as np

    # Extract the optimizers, ansatze, and the specified metric
    optimizers = ['SLSQP', 'P_BFGS', 'NELDER_MEAD', 'POWELL']
    ansatze = ['RealAmplitudes', 'TwoLocal', 'EfficientSU2']
    colors = ['blue', 'red', 'purple']  # Color map for ansatze
    markers = {'RealAmplitudes': 'o', 'TwoLocal': 's', 'EfficientSU2': '^'}

    # Data organization by optimizer and ansatz
    optimizer_data = {opt: {ansatz: [] for ansatz in ansatze} for opt in optimizers}
    failed_data = {opt: {ansatz: [] for ansatz in ansatze} for opt in optimizers}

    for entry in data:
        optimizer, value = entry
        opt, ansatz = optimizer.split('-')

        if value == 0:  # Mark as 'Did not converge'
            failed_data[opt][ansatz].append(entry)
        else:
            optimizer_data[opt][ansatz].append(value)

    # Determine the minimum positive value for plotting
    min_positive_value = min(
        value for opt_data in optimizer_data.values()
        for ansatz_data in opt_data.values()
        for value in ansatz_data if value > 0
    )
    nc_marker_value = min_positive_value * 0.1  # Marker for non-converging cases

    x_positions = np.arange(len(optimizers))
    offset = 0.1  # Base horizontal offset for non-converging cases
    vertical_offset = 0.5  # Vertical offset for crosses

    # Plot the failed cases (crosses) first
    for i, opt in enumerate(optimizers):
        for j, ansatz in enumerate(ansatze):
            failed_cases = failed_data[opt][ansatz]

            # Plot the non-converging cases
            if failed_cases:
                for k, _ in enumerate(failed_cases):
                    ax.scatter(
                        x_positions[i] + offset * (j - 1),  # Horizontal offset based on ansatz index
                        nc_marker_value * (1 + 0.1 * k),  # Small vertical offset for spreading
                        color=colors[j], marker='x', s=100, label=f'{ansatz} (NC)' if i == 0 and j == 0 else ""
                    )

    # Plot the metric values for converging cases
    for i, opt in enumerate(optimizers):
        for j, ansatz in enumerate(ansatze):
            values = optimizer_data[opt][ansatz]

            # Plot the metric values with specific markers for ansatze
            if values:
                ax.plot(
                    [x_positions[i]], np.abs(values),
                    marker=markers[ansatz], markersize=9, linestyle='-', color=colors[j],
                    label=ansatz if i == 0 else ""  # Only add the ansatz label once
                )

    # Set axis properties
    ax.set_xticks(x_positions)
    ax.set_xticklabels(optimizers)
    ax.set_ylabel(ylabel, fontsize=20)
    ax.tick_params(axis='x', labelsize=17)
    ax.tick_params(axis='y', labelsize=17)
    ax.grid(True)
    ax.legend(fontsize=15)

    # Set y-axis to log scale
    ax.set_yscale('log')

    # # Adjust y-axis limits to include non-converging marker
    # ax.set_ylim(bottom=nc_marker_value * 0.05)

## Get all the data for visualization

In [5]:
## For V = 1.1 (for N = 2 and 3)
# Get the gate counts
gate_counts_N_2_V_1 = [
    ('SLSQP-RealAmplitudes', 8),
    ('SLSQP-TwoLocal', 5),
    ('SLSQP-EfficientSU2', 8),
    ('P_BFGS-RealAmplitudes', 5),
    ('P_BFGS-TwoLocal', 5),
    ('P_BFGS-EfficientSU2', 5),
    ('NELDER_MEAD-RealAmplitudes', 5),
    ('NELDER_MEAD-TwoLocal', 5),
    ('NELDER_MEAD-EfficientSU2', 5),
    ('POWELL-RealAmplitudes', 14),
    ('POWELL-TwoLocal', 5),
    ('POWELL-EfficientSU2', 14),
]

gate_counts_N_3_V_1 = [
    ('SLSQP-RealAmplitudes', 9),
    ('SLSQP-TwoLocal', 9),
    ('SLSQP-EfficientSU2', 21),
    ('P_BFGS-RealAmplitudes', 15),
    ('P_BFGS-TwoLocal', 15),
    ('P_BFGS-EfficientSU2', 33),
    ('NELDER_MEAD-RealAmplitudes', 0),
    ('NELDER_MEAD-TwoLocal', 0),
    ('NELDER_MEAD-EfficientSU2', 0),
    ('POWELL-RealAmplitudes', 0),
    ('POWELL-TwoLocal', 0),
    ('POWELL-EfficientSU2', 0)
]

# Get the circuit depths
circuit_depths_N_2_V_1 = [
    ('SLSQP-RealAmplitudes', 5),
    ('SLSQP-TwoLocal', 3),
    ('SLSQP-EfficientSU2', 5),
    ('P_BFGS-RealAmplitudes', 3),
    ('P_BFGS-TwoLocal', 3),
    ('P_BFGS-EfficientSU2', 3),
    ('NELDER_MEAD-RealAmplitudes', 3),
    ('NELDER_MEAD-TwoLocal', 3),
    ('NELDER_MEAD-EfficientSU2', 3),
    ('POWELL-RealAmplitudes', 9),
    ('POWELL-TwoLocal', 3),
    ('POWELL-EfficientSU2', 9),
]

circuit_depths_N_3_V_1 = [
    ('SLSQP-RealAmplitudes', 5),
    ('SLSQP-TwoLocal', 5),
    ('SLSQP-EfficientSU2', 13),
    ('P_BFGS-RealAmplitudes', 9),
    ('P_BFGS-TwoLocal', 9),
    ('P_BFGS-EfficientSU2', 21),
    ('NELDER_MEAD-RealAmplitudes', 0),
    ('NELDER_MEAD-TwoLocal', 0),
    ('NELDER_MEAD-EfficientSU2', 0),
    ('POWELL-RealAmplitudes', 0),
    ('POWELL-TwoLocal', 0),
    ('POWELL-EfficientSU2', 0)
]

# Get the number of function calls
function_calls_N_2_V_1 = [
    ('SLSQP-RealAmplitudes', 90),
    ('SLSQP-TwoLocal', 153),
    ('SLSQP-EfficientSU2', 61),
    ('P_BFGS-RealAmplitudes', 135),
    ('P_BFGS-TwoLocal', 140),
    ('P_BFGS-EfficientSU2', 135),
    ('NELDER_MEAD-RealAmplitudes', 423),
    ('NELDER_MEAD-TwoLocal', 423),
    ('NELDER_MEAD-EfficientSU2', 423),
    ('POWELL-RealAmplitudes', 599),
    ('POWELL-TwoLocal', 759),
    ('POWELL-EfficientSU2', 880),
]

function_calls_N_3_V_1 = [
    ('SLSQP-RealAmplitudes', 241),
    ('SLSQP-TwoLocal', 342),
    ('SLSQP-EfficientSU2', 1548),
    ('P_BFGS-RealAmplitudes', 5280),
    ('P_BFGS-TwoLocal', 5120),
    ('P_BFGS-EfficientSU2', 2489),
    ('NELDER_MEAD-RealAmplitudes', 0),
    ('NELDER_MEAD-TwoLocal', 0),
    ('NELDER_MEAD-EfficientSU2', 0),
    ('POWELL-RealAmplitudes', 0),
    ('POWELL-TwoLocal', 0),
    ('POWELL-EfficientSU2', 0)
]

## For V = 5.5 (N = 2 and 3)
# Get the gate counts
gate_counts_N_2_V_5 = [
    ('SLSQP-RealAmplitudes', 11),
    ('SLSQP-TwoLocal', 5),
    ('SLSQP-EfficientSU2', 11),
    ('P_BFGS-RealAmplitudes', 11),
    ('P_BFGS-TwoLocal', 5),
    ('P_BFGS-EfficientSU2', 17),
    ('NELDER_MEAD-RealAmplitudes', 5),
    ('NELDER_MEAD-TwoLocal', 5),
    ('NELDER_MEAD-EfficientSU2', 5),
    ('POWELL-RealAmplitudes', 17),
    ('POWELL-TwoLocal', 5),
    ('POWELL-EfficientSU2', 8),
]

gate_counts_N_3_V_5 = [
    ('SLSQP-RealAmplitudes', 9),
    ('SLSQP-TwoLocal', 9),
    ('SLSQP-EfficientSU2', 21),
    ('P_BFGS-RealAmplitudes', 15),
    ('P_BFGS-TwoLocal', 9),
    ('P_BFGS-EfficientSU2', 15),
    ('NELDER_MEAD-RealAmplitudes', 9),
    ('NELDER_MEAD-TwoLocal', 9),
    ('NELDER_MEAD-EfficientSU2', 0),
    ('POWELL-RealAmplitudes', 0),
    ('POWELL-TwoLocal', 9),
    ('POWELL-EfficientSU2', 0)
]

# Get the circuit depths
circuit_depths_N_2_V_5 = [
    ('SLSQP-RealAmplitudes', 7),
    ('SLSQP-TwoLocal', 3),
    ('SLSQP-EfficientSU2', 7),
    ('P_BFGS-RealAmplitudes', 7),
    ('P_BFGS-TwoLocal', 3),
    ('P_BFGS-EfficientSU2', 11),
    ('NELDER_MEAD-RealAmplitudes', 3),
    ('NELDER_MEAD-TwoLocal', 3),
    ('NELDER_MEAD-EfficientSU2', 3),
    ('POWELL-RealAmplitudes', 11),
    ('POWELL-TwoLocal', 3),
    ('POWELL-EfficientSU2', 5),
]

circuit_depths_N_3_V_5 = [
    ('SLSQP-RealAmplitudes', 5),
    ('SLSQP-TwoLocal', 5),
    ('SLSQP-EfficientSU2', 13),
    ('P_BFGS-RealAmplitudes', 9),
    ('P_BFGS-TwoLocal', 5),
    ('P_BFGS-EfficientSU2', 9),
    ('NELDER_MEAD-RealAmplitudes', 5),
    ('NELDER_MEAD-TwoLocal', 5),
    ('NELDER_MEAD-EfficientSU2', 0),
    ('POWELL-RealAmplitudes', 0),
    ('POWELL-TwoLocal', 5),
    ('POWELL-EfficientSU2', 0)
]

# Get the number of function calls
function_calls_N_2_V_5 = [
    ('SLSQP-RealAmplitudes', 131),
    ('SLSQP-TwoLocal', 75),
    ('SLSQP-EfficientSU2', 130),
    ('P_BFGS-RealAmplitudes', 144),
    ('P_BFGS-TwoLocal', 95),
    ('P_BFGS-EfficientSU2', 169),
    ('NELDER_MEAD-RealAmplitudes', 181),
    ('NELDER_MEAD-TwoLocal', 181),
    ('NELDER_MEAD-EfficientSU2', 181),
    ('POWELL-RealAmplitudes', 1000),
    ('POWELL-TwoLocal', 492),
    ('POWELL-EfficientSU2', 798),
]

function_calls_N_3_V_5 = [
    ('SLSQP-RealAmplitudes', 205),
    ('SLSQP-TwoLocal', 205),
    ('SLSQP-EfficientSU2', 966),
    ('P_BFGS-RealAmplitudes', 4430),
    ('P_BFGS-TwoLocal', 959),
    ('P_BFGS-EfficientSU2', 1860),
    ('NELDER_MEAD-RealAmplitudes', 890),
    ('NELDER_MEAD-TwoLocal', 890),
    ('NELDER_MEAD-EfficientSU2', 0),
    ('POWELL-RealAmplitudes', 0),
    ('POWELL-TwoLocal', 1000),
    ('POWELL-EfficientSU2', 0)
]

## For V = 10.5
# Get the gate counts
gate_counts_N_2_V_10 = [
    ('SLSQP-RealAmplitudes', 5),
    ('SLSQP-TwoLocal', 5),
    ('SLSQP-EfficientSU2', 5),
    ('P_BFGS-RealAmplitudes', 5),
    ('P_BFGS-TwoLocal', 5),
    ('P_BFGS-EfficientSU2', 5),
    ('NELDER_MEAD-RealAmplitudes', 5),
    ('NELDER_MEAD-TwoLocal', 5),
    ('NELDER_MEAD-EfficientSU2', 5),
    ('POWELL-RealAmplitudes', 8),
    ('POWELL-TwoLocal', 5),
    ('POWELL-EfficientSU2', 8),
]

gate_counts_N_3_V_10 = [
    ('SLSQP-RealAmplitudes', 15),
    ('SLSQP-TwoLocal', 9),
    ('SLSQP-EfficientSU2', 15),
    ('P_BFGS-RealAmplitudes', 15),
    ('P_BFGS-TwoLocal', 9),
    ('P_BFGS-EfficientSU2', 15),
    ('NELDER_MEAD-RealAmplitudes', 9),
    ('NELDER_MEAD-TwoLocal', 9),
    ('NELDER_MEAD-EfficientSU2', 0),
    ('POWELL-RealAmplitudes', 15),
    ('POWELL-TwoLocal', 9),
    ('POWELL-EfficientSU2', 0)
]

# Get the circuit depths
circuit_depths_N_2_V_10 = [
    ('SLSQP-RealAmplitudes', 3),
    ('SLSQP-TwoLocal', 3),
    ('SLSQP-EfficientSU2', 3),
    ('P_BFGS-RealAmplitudes', 3),
    ('P_BFGS-TwoLocal', 3),
    ('P_BFGS-EfficientSU2', 3),
    ('NELDER_MEAD-RealAmplitudes', 3),
    ('NELDER_MEAD-TwoLocal', 3),
    ('NELDER_MEAD-EfficientSU2', 3),
    ('POWELL-RealAmplitudes', 5),
    ('POWELL-TwoLocal', 3),
    ('POWELL-EfficientSU2', 5),
]

circuit_depths_N_3_V_10 = [
    ('SLSQP-RealAmplitudes', 9),
    ('SLSQP-TwoLocal', 5),
    ('SLSQP-EfficientSU2', 9),
    ('P_BFGS-RealAmplitudes', 9),
    ('P_BFGS-TwoLocal', 5),
    ('P_BFGS-EfficientSU2', 9),
    ('NELDER_MEAD-RealAmplitudes', 5),
    ('NELDER_MEAD-TwoLocal', 5),
    ('NELDER_MEAD-EfficientSU2', 0),
    ('POWELL-RealAmplitudes', 9),
    ('POWELL-TwoLocal', 5),
    ('POWELL-EfficientSU2', 0)
]

# Get the number of function calls
function_calls_N_2_V_10 = [
    ('SLSQP-RealAmplitudes', 98),
    ('SLSQP-TwoLocal', 90),
    ('SLSQP-EfficientSU2', 98),
    ('P_BFGS-RealAmplitudes', 150),
    ('P_BFGS-TwoLocal', 105),
    ('P_BFGS-EfficientSU2', 150),
    ('NELDER_MEAD-RealAmplitudes', 218),
    ('NELDER_MEAD-TwoLocal', 218),
    ('NELDER_MEAD-EfficientSU2', 218),
    ('POWELL-RealAmplitudes', 968),
    ('POWELL-TwoLocal', 571),
    ('POWELL-EfficientSU2', 826),
]

function_calls_N_3_V_10 = [
    ('SLSQP-RealAmplitudes', 807),
    ('SLSQP-TwoLocal', 258),
    ('SLSQP-EfficientSU2', 1005),
    ('P_BFGS-RealAmplitudes', 1380),
    ('P_BFGS-TwoLocal', 1680),
    ('P_BFGS-EfficientSU2', 1110),
    ('NELDER_MEAD-RealAmplitudes', 1000),
    ('NELDER_MEAD-TwoLocal', 1000),
    ('NELDER_MEAD-EfficientSU2', 0),
    ('POWELL-RealAmplitudes', 1000),
    ('POWELL-TwoLocal', 463),
    ('POWELL-EfficientSU2', 0)
]

## Visualize the data for N = 2

In [7]:
# Create figure and axes for 6 subplots
fig, axs = plt.subplots(3, 3, figsize=(18, 15), dpi=600)  # Adjusted to 4 rows

# Plot gate counts
plot_metric(gate_counts_N_2_V_1, axs[0, 0], 'gate_count', 'Gate count')
axs[0, 0].set_title(r'$V = 1.1; N_{\mathrm{qubits}} = 2$', fontsize=17)
plot_metric(gate_counts_N_2_V_5, axs[0, 1], 'gate_count', 'Gate count')
axs[0, 1].set_title(r'$V = 5.5; N_{\mathrm{qubits}} = 2$', fontsize=17)
plot_metric(gate_counts_N_2_V_10, axs[0, 2], 'gate_count', 'Gate count')
axs[0, 2].set_title(r'$V = 10.5; N_{\mathrm{qubits}} = 2$', fontsize=17)

# Plot circuit depths
plot_metric(circuit_depths_N_2_V_1, axs[1, 0], 'circuit_depth', 'Circuit depth')
plot_metric(circuit_depths_N_2_V_5, axs[1, 1], 'circuit_depth', 'Circuit depth')
plot_metric(circuit_depths_N_2_V_10, axs[1, 2], 'circuit_depth', 'Circuit depth')

# Plot for function calls (\lambda_0)
plot_metric(function_calls_N_2_V_1, axs[2, 0], 'function_calls', 'Function calls')
plot_metric(function_calls_N_2_V_5, axs[2, 1], 'function_calls', 'Function calls')
plot_metric(function_calls_N_2_V_10, axs[2, 2], 'function_calls', 'Function calls')

# Adjust layout and show the plot
plt.tight_layout(pad=2.0)
plt.savefig('Resource estimates_zeromodes_N_2_Schlogl.pdf', bbox_inches = 'tight', dpi = 600)

## Visualize the data for N = 3

In [9]:
# Create figure and axes for 6 subplots
fig, axs = plt.subplots(3, 3, figsize=(18, 15), dpi=600)  # Adjusted to 4 rows

# Plot gate counts
plot_metric(gate_counts_N_3_V_1, axs[0, 0], 'gate_count', 'Gate count')
axs[0, 0].set_title(r'$V = 1.1; N_{\mathrm{qubits}} = 3$', fontsize=17)
plot_metric(gate_counts_N_3_V_5, axs[0, 1], 'gate_count', 'Gate count')
axs[0, 1].set_title(r'$V = 5.5; N_{\mathrm{qubits}} = 3$', fontsize=17)
plot_metric(gate_counts_N_3_V_10, axs[0, 2], 'gate_count', 'Gate count')
axs[0, 2].set_title(r'$V = 10.5; N_{\mathrm{qubits}} = 3$', fontsize=17)

# Plot circuit depths
plot_metric(circuit_depths_N_3_V_1, axs[1, 0], 'circuit_depth', 'Circuit depth')
plot_metric(circuit_depths_N_3_V_5, axs[1, 1], 'circuit_depth', 'Circuit depth')
plot_metric(circuit_depths_N_3_V_10, axs[1, 2], 'circuit_depth', 'Circuit depth')

# Plot for function calls (\lambda_0)
plot_metric(function_calls_N_3_V_1, axs[2, 0], 'function_calls', 'Function calls')
plot_metric(function_calls_N_3_V_5, axs[2, 1], 'function_calls', 'Function calls')
plot_metric(function_calls_N_3_V_10, axs[2, 2], 'function_calls', 'Function calls')

# Adjust layout and show the plot
plt.tight_layout(pad=2.0)
plt.savefig('Resource estimates_zeromodes_N_3_Schlogl.pdf', bbox_inches = 'tight', dpi = 600)

## Comparing expectation values

### Get all the data

In [11]:
## For V = 1.1
# For N = 2
expectation_values_N_2_V_1 = [
    # SLSQP
    ('SLSQP-RealAmplitudes', 1.47590866e-05),
    ('SLSQP-TwoLocal', 3.86938069e-06),
    ('SLSQP-EfficientSU2', 3.65833805e-06),

    # P-BFGS
    ('P_BFGS-RealAmplitudes', -1.01942786e-07),
    ('P_BFGS-TwoLocal', -2.23637969e-08),
    ('P_BFGS-EfficientSU2', -1.01942786e-07),

    # NELDER-MEAD
    ('NELDER_MEAD-RealAmplitudes', -1.54290939e-05),
    ('NELDER_MEAD-TwoLocal', -1.54290939e-05),
    ('NELDER_MEAD-EfficientSU2', -1.54290939e-05),

    # POWELL
    ('POWELL-RealAmplitudes', 6.57286142e-07),
    ('POWELL-TwoLocal', -3.59813277e-08),
    ('POWELL-EfficientSU2', 1.2512823e-06)
]

# For N = 3
expectation_values_N_3_V_1 = [
    # SLSQP
    ('SLSQP-RealAmplitudes', -0.00333661),
    ('SLSQP-TwoLocal', -0.00393305),
    ('SLSQP-EfficientSU2', 6.28929599e-05),

    # P-BFGS
    ('P_BFGS-RealAmplitudes', -0.00196205),
    ('P_BFGS-TwoLocal', 2.78240597e-05),
    ('P_BFGS-EfficientSU2', -6.09139538e-06),

    # NELDER-MEAD
    ('NELDER_MEAD-RealAmplitudes', 0),
    ('NELDER_MEAD-TwoLocal', 0),
    ('NELDER_MEAD-EfficientSU2', 0),

    # POWELL
    ('POWELL-RealAmplitudes', 0),
    ('POWELL-TwoLocal', 0),
    ('POWELL-EfficientSU2', 0)
]

## For V = 5.5
# For N = 2
expectation_values_N_2_V_5 = [
    # SLSQP
    ('SLSQP-RealAmplitudes', -6.84406188e-06),
    ('SLSQP-TwoLocal', -8.15942788e-06),
    ('SLSQP-EfficientSU2', 5.30984756e-06),

    # P-BFGS
    ('P_BFGS-RealAmplitudes', -6.35677962e-08),
    ('P_BFGS-TwoLocal', 4.37160805e-09),
    ('P_BFGS-EfficientSU2', 4.80653133e-08),

    # NELDER-MEAD
    ('NELDER_MEAD-RealAmplitudes', -1.18406504e-05),
    ('NELDER_MEAD-TwoLocal', -1.18406504e-05),
    ('NELDER_MEAD-EfficientSU2', -1.18406504e-05),

    # POWELL
    ('POWELL-RealAmplitudes', 1.56631202e-06),
    ('POWELL-TwoLocal', 1.23320874e-08),
    ('POWELL-EfficientSU2', 1.67647263e-06)
]

# For N = 3
expectation_values_N_3_V_5 = [
    # SLSQP
    ('SLSQP-RealAmplitudes', -0.00414173),
    ('SLSQP-TwoLocal', -0.00299129),
    ('SLSQP-EfficientSU2', -1.32308012e-05),

    # P-BFGS
    ('P_BFGS-RealAmplitudes', 2.57925068e-06),
    ('P_BFGS-TwoLocal', -0.00189429),
    ('P_BFGS-EfficientSU2', 4.93034982e-07),

    # NELDER-MEAD
    ('NELDER_MEAD-RealAmplitudes', -0.00417531),
    ('NELDER_MEAD-TwoLocal', -0.00417531),
    ('NELDER_MEAD-EfficientSU2', 0),  # 'No solution'

    # POWELL
    ('POWELL-RealAmplitudes', 0),  # 'No solution'
    ('POWELL-TwoLocal', -0.00167871),
    ('POWELL-EfficientSU2', 0)  # 'No solution'
]

## For V = 10.5
# For N = 2
expectation_values_N_2_V_10 = [
    # SLSQP
    ('SLSQP-RealAmplitudes', -8.278446e-07),
    ('SLSQP-TwoLocal', 1.82685057e-06),
    ('SLSQP-EfficientSU2', -8.278446e-07),

    # P-BFGS
    ('P_BFGS-RealAmplitudes', -8.63430482e-09),
    ('P_BFGS-TwoLocal', -1.67120046e-08),
    ('P_BFGS-EfficientSU2', -8.63430482e-09),

    # NELDER-MEAD
    ('NELDER_MEAD-RealAmplitudes', -1.56880831e-06),
    ('NELDER_MEAD-TwoLocal', -1.56880831e-06),
    ('NELDER_MEAD-EfficientSU2', -1.56880831e-06),

    # POWELL
    ('POWELL-RealAmplitudes', -3.07530503e-07),
    ('POWELL-TwoLocal', -8.79740401e-09),
    ('POWELL-EfficientSU2', 1.24151515e-06)
]

# For N = 3
expectation_values_N_3_V_10 = [
    # SLSQP
    ('SLSQP-RealAmplitudes', -0.00015868),
    ('SLSQP-TwoLocal', -0.05321201),
    ('SLSQP-EfficientSU2', -4.52762851e-06),

    # P-BFGS
    ('P_BFGS-RealAmplitudes', -6.52333184e-06),
    ('P_BFGS-TwoLocal', -0.05331227),
    ('P_BFGS-EfficientSU2', 4.33193428e-09),

    # NELDER-MEAD
    ('NELDER_MEAD-RealAmplitudes', -0.03927206),
    ('NELDER_MEAD-TwoLocal', -0.03927206),
    ('NELDER_MEAD-EfficientSU2', 0),  # 'No solution'

    # POWELL
    ('POWELL-RealAmplitudes', 0.01092014),
    ('POWELL-TwoLocal', -0.05537051),
    ('POWELL-EfficientSU2', 0)  # 'No solution'
]

## Visualize the expectation values data (for N = 2 and 3)

In [13]:
# Create figure and axes for 6 subplots
fig, axs = plt.subplots(3, 2, figsize=(18, 18), dpi=600)  # Adjusted to 4 rows

# Plot expectation values
plot_metric_log(expectation_values_N_2_V_1, axs[0, 0], 'expectation_values', r'$\langle Q \rangle$')
axs[0, 0].set_title(r'$V = 1.1; N_{\mathrm{qubits}} = 2$', fontsize=19)
plot_metric_log(expectation_values_N_3_V_1, axs[0, 1], 'expectation_values', r'$\langle Q \rangle$')
axs[0, 1].set_title(r'$V = 1.1; N_{\mathrm{qubits}} = 3$', fontsize=19)

# Plot expectation values
plot_metric_log(expectation_values_N_2_V_5, axs[1, 0], 'expectation_values', r'$\langle Q \rangle$')
axs[1, 0].set_title(r'$V = 5.5; N_{\mathrm{qubits}} = 2$', fontsize=19)
plot_metric_log(expectation_values_N_3_V_5, axs[1, 1], 'expectation_values', r'$\langle Q \rangle$')
axs[1, 1].set_title(r'$V = 5.5; N_{\mathrm{qubits}} = 3$', fontsize=19)

# Plot expectation values
plot_metric_log(expectation_values_N_2_V_10, axs[2, 0], 'expectation_values', r'$\langle Q \rangle$')
axs[2, 0].set_title(r'$V = 10.5; N_{\mathrm{qubits}} = 2$', fontsize=19)
plot_metric_log(expectation_values_N_3_V_10, axs[2, 1], 'expectation_values', r'$\langle Q \rangle$')
axs[2, 1].set_title(r'$V = 10.5; N_{\mathrm{qubits}} = 3$', fontsize=19)

# Adjust layout and show the plot
plt.tight_layout(pad=2.0)
plt.savefig('Expectation values comparison_zeromodes_Schlogl.pdf', bbox_inches = 'tight', dpi = 600)

### Comparing the no. of variational parameters for different ansatz-optimizer pairs

### Relevant functions

In [5]:
def extract_variational_parameters(data, num_qubits):
    """
    Constructs the ansatz for each ansatz-optimizer pair with specified depths and extracts
    the number of variational parameters using Qiskit.

    Parameters:
        data (dict): A dictionary where keys are ansatz-optimizer pairs (e.g., "SLSQP-RealAmplitudes") and
                     values are the minimum ansatz depths.
        num_qubits (int): The number of qubits used in the circuit.

    Returns:
        list: A list of tuples of the form (ansatz-optimizer, num_parameters).
    """
    variational_params = []

    for ansatz_optimizer, depth in data.items():
        if depth == 'Did not converge':  # Handle cases where depth is not available
            num_parameters = 0
        else:
            optimizer, ansatz = ansatz_optimizer.split('-')
            
            # Construct the ansatz based on the specified type
            if ansatz == "RealAmplitudes":
                circuit = RealAmplitudes(num_qubits, entanglement='full', reps=depth)
            elif ansatz == "TwoLocal":
                circuit = TwoLocal(num_qubits, rotation_blocks=['ry'], entanglement_blocks='cx', reps=depth)
            elif ansatz == "EfficientSU2":
                circuit = EfficientSU2(num_qubits, su2_gates = ['ry'], entanglement='sca', reps=depth)
            else:
                # Default if ansatz type is unknown
                circuit = None
            
            # Get the number of parameters if the circuit was successfully constructed
            num_parameters = circuit.num_parameters if circuit else 0
        
        variational_params.append((ansatz_optimizer, num_parameters))

    return variational_params

### Extracting all the data

In [7]:
## For 2 qubits
# For V = 1.1
ansatz_depths_N_2_V_1 = {'SLSQP-RealAmplitudes': 2, 'SLSQP-TwoLocal': 1, 'SLSQP-EfficientSU2': 2, 'P_BFGS-RealAmplitudes': 1, 'P_BFGS-TwoLocal': 1, 'P_BFGS-EfficientSU2': 1, 'NELDER_MEAD-RealAmplitudes': 1, 'NELDER_MEAD-TwoLocal': 1, 'NELDER_MEAD-EfficientSU2': 1, 'POWELL-RealAmplitudes': 4, 'POWELL-TwoLocal': 1, 'POWELL-EfficientSU2': 4}

# For V = 5.5
ansatz_depths_N_2_V_5 = {'SLSQP-RealAmplitudes': 3, 'SLSQP-TwoLocal': 1, 'SLSQP-EfficientSU2': 3, 'P_BFGS-RealAmplitudes': 3, 'P_BFGS-TwoLocal': 1, 'P_BFGS-EfficientSU2': 5, 'NELDER_MEAD-RealAmplitudes': 1, 'NELDER_MEAD-TwoLocal': 1, 'NELDER_MEAD-EfficientSU2': 1, 'POWELL-RealAmplitudes': 5, 'POWELL-TwoLocal': 1, 'POWELL-EfficientSU2': 2}

# For V = 10.5
ansatz_depths_N_2_V_10 = {'SLSQP-RealAmplitudes': 3, 'SLSQP-TwoLocal': 1, 'SLSQP-EfficientSU2': 3, 'P_BFGS-RealAmplitudes': 3, 'P_BFGS-TwoLocal': 1, 'P_BFGS-EfficientSU2': 5, 'NELDER_MEAD-RealAmplitudes': 1, 'NELDER_MEAD-TwoLocal': 1, 'NELDER_MEAD-EfficientSU2': 1, 'POWELL-RealAmplitudes': 5, 'POWELL-TwoLocal': 1, 'POWELL-EfficientSU2': 2}

## For 3 qubits
# For V = 1.1
ansatz_depths_N_3_V_1 = {'SLSQP-RealAmplitudes': 3, 'SLSQP-TwoLocal': 1, 'SLSQP-EfficientSU2': 3, 'P_BFGS-RealAmplitudes': 3, 'P_BFGS-TwoLocal': 1, 'P_BFGS-EfficientSU2': 5, 'NELDER_MEAD-RealAmplitudes': 1, 'NELDER_MEAD-TwoLocal': 1, 'NELDER_MEAD-EfficientSU2': 1, 'POWELL-RealAmplitudes': 5, 'POWELL-TwoLocal': 1, 'POWELL-EfficientSU2': 2}

# For V = 5.5
ansatz_depths_N_3_V_5 = {'SLSQP-RealAmplitudes': 1, 'SLSQP-TwoLocal': 1, 'SLSQP-EfficientSU2': 3, 'P_BFGS-RealAmplitudes': 2, 'P_BFGS-TwoLocal': 1, 'P_BFGS-EfficientSU2': 2, 'NELDER_MEAD-RealAmplitudes': 1, 'NELDER_MEAD-TwoLocal': 1, 'NELDER_MEAD-EfficientSU2': 'Did not converge', 'POWELL-RealAmplitudes': 'Did not converge', 'POWELL-TwoLocal': 1, 'POWELL-EfficientSU2': 'Did not converge'}

# For V = 10.5
ansatz_depths_N_3_V_10 = {'SLSQP-RealAmplitudes': 2, 'SLSQP-TwoLocal': 1, 'SLSQP-EfficientSU2': 2, 'P_BFGS-RealAmplitudes': 2, 'P_BFGS-TwoLocal': 1, 'P_BFGS-EfficientSU2': 2, 'NELDER_MEAD-RealAmplitudes': 1, 'NELDER_MEAD-TwoLocal': 1, 'NELDER_MEAD-EfficientSU2': 'Did not converge', 'POWELL-RealAmplitudes': 2, 'POWELL-TwoLocal': 1, 'POWELL-EfficientSU2': 'Did not converge'}

## Extract the data as lists
# For 2 qubits
parameters_N_2_V_1 = extract_variational_parameters(ansatz_depths_N_2_V_1, 2) # for 1.1
parameters_N_2_V_5 = extract_variational_parameters(ansatz_depths_N_2_V_5, 2) # for 5.5
parameters_N_2_V_10 = extract_variational_parameters(ansatz_depths_N_2_V_10, 2) # for 10.5

# For 3 qubits
parameters_N_3_V_1 = extract_variational_parameters(ansatz_depths_N_3_V_1, 3) # for 1.1
parameters_N_3_V_5 = extract_variational_parameters(ansatz_depths_N_3_V_5, 3) # for 5.5
parameters_N_3_V_10 = extract_variational_parameters(ansatz_depths_N_3_V_10, 3) # for 10.5

### Printing the no. of variational parameters

In [9]:
## For 2 qubits
print('The no. of variational parameters for 2 qubits and V = 1.1 are:')
print(parameters_N_2_V_1)
print()

print('The no. of variational parameters for 2 qubits and V = 5.5 are:')
print(parameters_N_2_V_5)
print()

print('The no. of variational parameters for 2 qubits and V = 10.5 are:')
print(parameters_N_2_V_10)
print()

## For 3 qubits
print('The no. of variational parameters for 3 qubits and V = 1.1 are:')
print(parameters_N_3_V_1)
print()

print('The no. of variational parameters for 3 qubits and V = 5.5 are:')
print(parameters_N_3_V_5)
print()

print('The no. of variational parameters for 3 qubits and V = 10.5 are:')
print(parameters_N_3_V_10)
print()

The no. of variational parameters for 2 qubits and V = 1.1 are:
[('SLSQP-RealAmplitudes', 6), ('SLSQP-TwoLocal', 4), ('SLSQP-EfficientSU2', 6), ('P_BFGS-RealAmplitudes', 4), ('P_BFGS-TwoLocal', 4), ('P_BFGS-EfficientSU2', 4), ('NELDER_MEAD-RealAmplitudes', 4), ('NELDER_MEAD-TwoLocal', 4), ('NELDER_MEAD-EfficientSU2', 4), ('POWELL-RealAmplitudes', 10), ('POWELL-TwoLocal', 4), ('POWELL-EfficientSU2', 10)]

The no. of variational parameters for 2 qubits and V = 5.5 are:
[('SLSQP-RealAmplitudes', 8), ('SLSQP-TwoLocal', 4), ('SLSQP-EfficientSU2', 8), ('P_BFGS-RealAmplitudes', 8), ('P_BFGS-TwoLocal', 4), ('P_BFGS-EfficientSU2', 12), ('NELDER_MEAD-RealAmplitudes', 4), ('NELDER_MEAD-TwoLocal', 4), ('NELDER_MEAD-EfficientSU2', 4), ('POWELL-RealAmplitudes', 12), ('POWELL-TwoLocal', 4), ('POWELL-EfficientSU2', 6)]

The no. of variational parameters for 2 qubits and V = 10.5 are:
[('SLSQP-RealAmplitudes', 8), ('SLSQP-TwoLocal', 4), ('SLSQP-EfficientSU2', 8), ('P_BFGS-RealAmplitudes', 8), ('P_BFGS-

### Visualization of data

### For all system volumes

In [17]:
# Create figure and axes for 6 subplots
fig, axs = plt.subplots(2, 3, figsize=(18, 12), dpi=600) 

# Plot metrics for 2 qubits
plot_metric(parameters_N_2_V_1, axs[0, 0], 'variational_parameters', 'No. of variational parameters')
axs[0, 0].set_title(r'$V = 1.1; N_{\mathrm{qubits}} = 2$', fontsize=18)
plot_metric(parameters_N_2_V_5, axs[0, 1], 'variational_parameters', 'No. of variational parameters')
axs[0, 1].set_title(r'$V = 5.5; N_{\mathrm{qubits}} = 2$', fontsize=18)
plot_metric(parameters_N_2_V_10, axs[0, 2], 'variational_parameters', 'No. of variational parameters')
axs[0, 2].set_title(r'$V = 10.5; N_{\mathrm{qubits}} = 2$', fontsize=18)

# Plot metrics 3 qubits
plot_metric(parameters_N_3_V_1, axs[1, 0], 'variational_parameters', 'No. of variational parameters')
axs[1, 0].set_title(r'$V = 1.1; N_{\mathrm{qubits}} = 3$', fontsize=18)
plot_metric(parameters_N_3_V_5, axs[1, 1], 'variational_parameters', 'No. of variational parameters')
axs[1, 1].set_title(r'$V = 5.5; N_{\mathrm{qubits}} = 3$', fontsize=18)
plot_metric(parameters_N_3_V_10, axs[1, 2], 'variational_parameters', 'No. of variational parameters')
axs[1, 2].set_title(r'$V = 10.5; N_{\mathrm{qubits}} = 3$', fontsize=18)

# Adjust layout and show the plot
plt.tight_layout(pad=2.0)
plt.show()